# Init

In [1]:
import datetime
import openpyxl
import os
import random
import time
import pandas as pd
import traceback
import arachnae
from selenium import webdriver
from selenium.webdriver.firefox.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from webdriver_manager.firefox import GeckoDriverManager
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.chrome.service import Service as ChromeService
# from fast_to_sql import fast_to_sql as fts

# TODO(make a logger to convert output into txt in ubuntu)
# TODO(try except finally)



## Time keeper
start_time1 = time.time()
print("\nStarting Instagram Selenium Script...\n")

## Akun Fake
USERNAME= arachnae.instagram_acc_3
PASSWORD= arachnae.instagram_pass_3

## Save path
datepath = datetime.date.today().strftime("%Y-%m-%d")
# datepath = '2023-04-24'
savefilepath = f"D:\\OneDrive\\1_bankmega\\scraping_results\\{datepath}"
os.makedirs(savefilepath, exist_ok=True)
path = f'{savefilepath}\\{datepath} Scraping Instagram All Banks.xlsx'


## workbook
# writer = pd.ExcelWriter(f'{savefilepath}\\{datepath} Scraping Instagram All Banks.xlsx',
#                         engine='xlsxwriter',
#                         engine_kwargs={'options': {'strings_to_urls': False, 'strings_to_numbers':False}})

# with pd.ExcelWriter(path) as writer:
#     writer.book = openpyxl.load_workbook(path)
#     df.to_excel(writer, sheet_name='')
#     df2.to_excel(writer, sheet_name='new_sheet2')


## Datetime
# strftime : datetime to string
# strptime : string to datetime
now_dt = datetime.datetime.now().strftime("%Y-%m-%dT%H:%M:%S.%fZ")

# change format to string
# awal = (datetime.datetime.now() - datetime.timedelta(hours= 7+1+ 7*24)).strftime("%Y-%m-%dT%H:%M:%S.%fZ")
# akhir = (datetime.datetime.now() - datetime.timedelta(hours= 7+1)).strftime("%Y-%m-%dT%H:%M:%S.%fZ")
awal = (datetime.datetime(2023, 4, 17, 0, 0, 0) - datetime.timedelta(hours= 7)).strftime("%Y-%m-%dT%H:%M:%S.%fZ")
akhir = (datetime.datetime(2023, 4, 23, 23, 59, 59) - datetime.timedelta(hours= 7)).strftime("%Y-%m-%dT%H:%M:%S.%fZ")


# string > datetime > string
# awal_mod = (datetime.datetime.now().replace(day=1) - datetime.timedelta(hours= 7+1)).strftime("%Y-%m-%dT%H:%M:%S.%fZ")
awal_mod = (datetime.datetime(2023, 5, 1, 0, 0, 0).replace(day=1) - datetime.timedelta(hours= 7)).strftime("%Y-%m-%dT%H:%M:%S.%fZ")

# string > datetime
# cutoff awal = every 1st
# cutoff akhir = every sunday of last week
cutoff_awal = datetime.datetime.strptime(awal_mod, "%Y-%m-%dT%H:%M:%S.%fZ") # awal_mod (tanggal 1) or awal (first day of the week)
cutoff_akhir = datetime.datetime.strptime(akhir, "%Y-%m-%dT%H:%M:%S.%fZ")

# string > datetime
# comment awal = every monday
# comment akhir = every sunday
comment_awal = datetime.datetime.strptime(awal, "%Y-%m-%dT%H:%M:%S.%fZ")
comment_akhir = datetime.datetime.strptime(akhir, "%Y-%m-%dT%H:%M:%S.%fZ")

print("now:",now_dt,"\ncutoff_awal:",cutoff_awal,"\ncutoff_akhir:",cutoff_akhir,"\ncomment_awal:",comment_awal,"\ncomment_akhir:",comment_akhir,"\n")


## Random
rand_precision = 0.01
f = round(1/rand_precision)
randtime_1 = random.randrange(round(3.01*f), round(5.99*f), round(0.01*f)) / f
randtime_2 = random.randrange(round(10.01*f), round(14.99*f), round(0.01*f)) / f

ModuleNotFoundError: No module named 'arachnae'

In [2]:
## Selenium Config
chrome_options = webdriver.ChromeOptions()
prefs = {"profile.default_content_setting_values.notifications" : 2}
chrome_options.add_experimental_option("prefs",prefs)
chrome_options.add_argument("start-maximized")

# r"D:\Downloads\chromedriver_win32\chromedriver.exe"
# driver= webdriver.Chrome(executable_path=ChromeDriverManager().install(), chrome_options=chrome_options)
service = ChromeService(executable_path=ChromeDriverManager().install())
driver = webdriver.Chrome(service=service, options=chrome_options)



## Login
driver.get("http://www.instagram.com")
time.sleep(2.3)
username = WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.CSS_SELECTOR, "input[name='username']")))
password = WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.CSS_SELECTOR, "input[name='password']")))
username.clear()
username.send_keys(USERNAME)
time.sleep(2.12)
password.clear()
password.send_keys(PASSWORD)
time.sleep(3.35)
button = WebDriverWait(driver, 2).until(EC.element_to_be_clickable((By.CSS_SELECTOR, "button[type='submit']"))).click()
time.sleep(5.35)

In [3]:
## Function
def get_comments(username: str, driver: webdriver, cutoff_awal: datetime.datetime, cutoff_akhir: datetime.datetime, comment_awal: datetime.datetime, comment_akhir: datetime.datetime):
    try:
        user_names = []
        comment_ids = []
        user_comments = []
        comment_date = []
        post_date = []
        post_url = []
        pinned_post_counter=0
        

        driver.get(f"https://www.instagram.com/{username}/")
        time.sleep(randtime_1)

        # start from latest post then click next until cutoff (first block to be exact)
        latest_post = WebDriverWait(driver, timeout=40).until(lambda d: d.find_element(By.CLASS_NAME,"_aabd"))
        latest_post.click()
        while True:
            time.sleep(3.53)
            post_time = WebDriverWait(driver, timeout=40).until(lambda d: d.find_element(By.CLASS_NAME,"_aaqe"))
        
            if (datetime.datetime.strptime(post_time.get_attribute("datetime"), "%Y-%m-%dT%H:%M:%S.%fZ") < cutoff_awal or datetime.datetime.strptime(post_time.get_attribute("datetime"), "%Y-%m-%dT%H:%M:%S.%fZ") > cutoff_akhir) and pinned_post_counter <= 6:
                pinned_post_counter +=1
                time.sleep(0.72)
                next_button = WebDriverWait(driver, timeout=40).until(lambda d: d.find_element(By.CLASS_NAME,"_aaqg"))
                next_button.click()
        

            elif datetime.datetime.strptime(post_time.get_attribute("datetime"), "%Y-%m-%dT%H:%M:%S.%fZ") <= cutoff_akhir and datetime.datetime.strptime(post_time.get_attribute("datetime"), "%Y-%m-%dT%H:%M:%S.%fZ") >= cutoff_awal:
                print('\n')
                try:
                    #print(datetime.strptime(post_time.get_attribute("datetime"), "%Y-%m-%dT%H:%M:%S.%fZ"))
                    time.sleep(3)
                    
                    # "Load more comments" until end
                    i=1
                    while True:
                        try:
                            WebDriverWait(driver, timeout=randtime_1).until(EC.element_to_be_clickable((By.XPATH, "/html/body/div[2]/div/div/div[3]/div/div/div[1]/div/div[3]/div/div/div/div/div[2]/div/article/div/div[2]/div/div/div[2]/div[1]/ul/li/div"))).click()
                            time.sleep(randtime_1)
                            print(f"'LOAD MORE COMMENTS' button is clicked. #{i}")
                            i+=1
                            
                        except:
                            print("No more 'LOAD MORE COMMENTS' button to be clicked\n")
                            break
                    

                    # "View Replies", wait until all located                
                    view_reply_buttons = driver.find_elements(By.CSS_SELECTOR, 'li > ul > li > div > button[class="_acan _acao _acas _aj1-"]')
                    
                    j=1
                    for button in range(len(view_reply_buttons)):
                        view_reply_buttons[button].click()
                        print(f"'VIEW REPLIES' button is clicked. #{j}")
                        j+=1
                        time.sleep(randtime_1)
                    print("No more 'VIEW REPLIES' button to be clicked\n")
                    
                except Exception as e:
                    print(e)
                    pass
                
                time.sleep(randtime_1)

                comment = driver.find_elements(By.XPATH, '//ul[@class="_a9ym"]/div/li/div[@class="_a9zm"]')
                
                for i,c in enumerate(comment):
                    container = c.find_element(By.XPATH,'.//div[@class="_a9zr"]')
                    comment_time = c.find_element(By.XPATH,'.//a/time[contains(@class,"_a9ze _a9zf")]')

                    if  datetime.datetime.strptime(comment_time.get_attribute("datetime"), "%Y-%m-%dT%H:%M:%S.%fZ") <= comment_akhir and datetime.datetime.strptime(comment_time.get_attribute("datetime"), "%Y-%m-%dT%H:%M:%S.%fZ") >= comment_awal :  
                        name = container.find_element(By.CLASS_NAME,"_a9zc").text
                        content = container.find_elements(By.CLASS_NAME,"_a9zs")[0].text
                        content = content.replace("\n", " ").strip().rstrip()

                        commentid_xpath = ".//a[@role='link' and .//time[contains(@class,'_a9ze _a9zf')]]"
                        commentid = c.find_element(By.XPATH, commentid_xpath).get_attribute("href")

                        comments_date = datetime.datetime.strptime(comment_time.get_attribute("datetime"), "%Y-%m-%dT%H:%M:%S.%fZ")
                        postdate = datetime.datetime.strptime(post_time.get_attribute("datetime"), "%Y-%m-%dT%H:%M:%S.%fZ")

                        user_names.append(name)
                        comment_ids.append(commentid)
                        comment_date.append(comments_date)
                        user_comments.append(content)
                        post_date.append(postdate)
                        post_url.append(driver.current_url)

                        print(i+1,";",commentid,";",comments_date,";",name,";",content,";",postdate,";",driver.current_url)

                    else:
                        pass
                    

            elif datetime.datetime.strptime(post_time.get_attribute("datetime"), "%Y-%m-%dT%H:%M:%S.%fZ") < cutoff_awal:
                break  

            # click next button
            time.sleep(randtime_1)
            next_button = WebDriverWait(driver, timeout=3*randtime_1).until(lambda d: d.find_element(By.CLASS_NAME,"_aaqg"))
            next_button.click()
    
        return user_names, comment_ids, user_comments, post_date, post_url, comment_date # comment_ids,

    except:
        print(f"Error: Saving current scraped comments for username: {username}\n")
        print(traceback.format_exc())
        # user_names = ['n/a']
        # comment_ids = ['n/a']
        # user_comments = ['n/a']
        # comment_date = ['1970-01-01 00:00:00']
        # post_date = ['n/a']
        # post_url = ['1970-01-01 00:00:00']
        return user_names, comment_ids, user_comments, post_date, post_url, comment_date # comment_ids,
        pass


# Convert datetime format
# dt > utc+7 > str
def datetime_format(comment_date_column):
    """
    change datetime format and convert to UTC+7
    `comment_date_column`: column of comment_date
    """
    for i in range(len(comment_date_column)):
        comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")
        
    return comment_date_column


# Batch 1 (Mega, OCBC, DBS)

In [4]:
## 1. Bank Mega
print('\nStart Scraping Instagram Bank Mega...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="bankmegaid", driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_mega = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"]) # "comment_id",
df_mega = df_mega[df_mega["name"] != "bankmegaid\nVerified"]
df_mega.reset_index(drop=True, inplace=True)
df_mega["bank"] = "Bank Mega"
df_mega["comment_date"] = datetime_format(df_mega["comment_date"])

with pd.ExcelWriter(path, engine='openpyxl') as writer:
    df_mega.to_excel(writer, sheet_name="Bank Mega")


## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram Bank Mega\n")

time.sleep(randtime_1*randtime_2)



## 2. Bank OCBC NISP
print('\nStart Scraping Instagram Bank OCBC NISP...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="ocbc_nisp",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_ocbc = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_ocbc = df_ocbc[df_ocbc["name"] != "ocbc_nisp\nVerified"]
df_ocbc.reset_index(drop=True, inplace=True)
df_ocbc["bank"] = "OCBC NISP"
df_ocbc["comment_date"] = datetime_format(df_ocbc["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    df_ocbc.to_excel(writer, sheet_name="Bank OCBC")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram Bank OCBC\n")

time.sleep(randtime_1*randtime_2)



## 3. DBS Bank
print('\nStart Scraping Instagram DBS Bank...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="dbsbankid", driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_dbs = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_dbs = df_dbs[df_dbs["name"] != "dbsbankid\nVerified"]
df_dbs.reset_index(drop=True, inplace=True)
df_dbs["bank"] = "DBS Bank"
df_dbs["comment_date"] = datetime_format(df_dbs["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_dbs.to_excel(writer, sheet_name="DBS Bank")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram DBS Bank\n")

time.sleep(randtime_1*randtime_2)


Start Scraping Instagram Bank Mega...



'LOAD MORE COMMENTS' button is clicked. #1
No more 'LOAD MORE COMMENTS' button to be clicked

'VIEW REPLIES' button is clicked. #1
'VIEW REPLIES' button is clicked. #2
'VIEW REPLIES' button is clicked. #3
'VIEW REPLIES' button is clicked. #4
'VIEW REPLIES' button is clicked. #5
'VIEW REPLIES' button is clicked. #6
'VIEW REPLIES' button is clicked. #7
No more 'VIEW REPLIES' button to be clicked

1 ; https://www.instagram.com/p/CrNBqcsSKFJ/c/17898223310720271/ ; 2023-04-20 13:38:04 ; adeva312 ; Bank Mega Admin....tlg segera kasih solusi yg masuk akal utk kesalahan yg kalian buat. Jangan seenaknya menyuruh org menanggung biaya atas kesalahan dan ketidak profesionalan dr pihak bank Mega ; 2023-04-19 04:00:05 ; https://www.instagram.com/p/CrNBqcsSKFJ/
2 ; https://www.instagram.com/p/CrNBqcsSKFJ/c/18003172354733959/ ; 2023-04-23 15:22:59 ; tika_kusnia ; Mau jadi kek Adi 😍 aamiin insyaAllah semoga bisa ngurangi sifat konsumtif 😂 ; 2023-04-19 04:00:05 

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 102.82 minutes

...Finished Scraping Instagram Bank Mega


Start Scraping Instagram Bank OCBC NISP...



'LOAD MORE COMMENTS' button is clicked. #1
'LOAD MORE COMMENTS' button is clicked. #2
'LOAD MORE COMMENTS' button is clicked. #3
'LOAD MORE COMMENTS' button is clicked. #4
'LOAD MORE COMMENTS' button is clicked. #5
'LOAD MORE COMMENTS' button is clicked. #6
'LOAD MORE COMMENTS' button is clicked. #7
'LOAD MORE COMMENTS' button is clicked. #8
'LOAD MORE COMMENTS' button is clicked. #9
'LOAD MORE COMMENTS' button is clicked. #10
'LOAD MORE COMMENTS' button is clicked. #11
'LOAD MORE COMMENTS' button is clicked. #12
'LOAD MORE COMMENTS' button is clicked. #13
'LOAD MORE COMMENTS' button is clicked. #14
'LOAD MORE COMMENTS' button is clicked. #15
'LOAD MORE COMMENTS' button is clicked. #16
'LOAD MORE COMMENTS' button is clicked. #17
'LOAD MORE COMMENTS' button is clicked. #18
'LOAD MORE COMMENTS' button is clicked. #19
'LOAD MORE COMMENTS' button is clicked. #20
'LOAD MOR

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 16.38 minutes

...Finished Scraping Instagram Bank OCBC


Start Scraping Instagram DBS Bank...



'LOAD MORE COMMENTS' button is clicked. #1
'LOAD MORE COMMENTS' button is clicked. #2
'LOAD MORE COMMENTS' button is clicked. #3
'LOAD MORE COMMENTS' button is clicked. #4
'LOAD MORE COMMENTS' button is clicked. #5
'LOAD MORE COMMENTS' button is clicked. #6
'LOAD MORE COMMENTS' button is clicked. #7
'LOAD MORE COMMENTS' button is clicked. #8
'LOAD MORE COMMENTS' button is clicked. #9
'LOAD MORE COMMENTS' button is clicked. #10
'LOAD MORE COMMENTS' button is clicked. #11
'LOAD MORE COMMENTS' button is clicked. #12
'LOAD MORE COMMENTS' button is clicked. #13
'LOAD MORE COMMENTS' button is clicked. #14
'LOAD MORE COMMENTS' button is clicked. #15
'LOAD MORE COMMENTS' button is clicked. #16
'LOAD MORE COMMENTS' button is clicked. #17
'LOAD MORE COMMENTS' button is clicked. #18
'LOAD MORE COMMENTS' button is clicked. #19
'LOAD MORE COMMENTS' button is clicked. #20
'LOAD MORE COMME

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 57.88 minutes

...Finished Scraping Instagram DBS Bank



# Batch 2 (Permata, CIMB, Danamon)

In [5]:
## 4. Permata Bank
print('\nStart Scraping Instagram Permata Bank...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="permatabank", driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_permata = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_permata = df_permata[df_permata["name"] != "permatabank\nVerified"]
df_permata.reset_index(drop=True, inplace=True)
df_permata["bank"] = "Permata Bank"
df_permata["comment_date"] = datetime_format(df_permata["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_permata.to_excel(writer, sheet_name="Permata Bank")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram Permata Bank\n")

time.sleep(randtime_1*randtime_2)



## 5. CIMB Niaga
print('\nStart Scraping Instagram CIMB Niaga...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="cimb_niaga",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_cimb = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_cimb = df_cimb[df_cimb["name"] != "cimb_niaga\nVerified"]
df_cimb.reset_index(drop=True, inplace=True)
df_cimb["bank"] = "CIMB Niaga"
df_cimb["comment_date"] = datetime_format(df_cimb["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_cimb.to_excel(writer, sheet_name="CIMB Niaga")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram CIMB Niaga\n")

time.sleep(randtime_1*randtime_2)



## 6. Bank Danamon
print('\nStart Scraping Instagram Bank Danamon...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="mydanamon",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_danamon = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_danamon = df_danamon[df_danamon["name"] != "mydanamon\nVerified"]
df_danamon.reset_index(drop=True, inplace=True)
df_danamon["bank"] = "Bank Danamon"
df_danamon["comment_date"] = datetime_format(df_danamon["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_danamon.to_excel(writer, sheet_name="Bank Danamon")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram Bank Danamon\n")

time.sleep(randtime_1*randtime_2)


Start Scraping Instagram Permata Bank...



No more 'LOAD MORE COMMENTS' button to be clicked

No more 'VIEW REPLIES' button to be clicked



No more 'LOAD MORE COMMENTS' button to be clicked

'VIEW REPLIES' button is clicked. #1
No more 'VIEW REPLIES' button to be clicked

2 ; https://www.instagram.com/p/CrXM1WZvg5a/c/17986866388954182/ ; 2023-04-23 03:13:13 ; aafermana ; 🔥🔥🔥🔥 ; 2023-04-23 02:50:05 ; https://www.instagram.com/p/CrXM1WZvg5a/
3 ; https://www.instagram.com/p/CrXM1WZvg5a/c/17990372020808998/ ; 2023-04-23 02:52:01 ; dwi_nings ; ❤️❤️ ; 2023-04-23 02:50:05 ; https://www.instagram.com/p/CrXM1WZvg5a/


No more 'LOAD MORE COMMENTS' button to be clicked

'VIEW REPLIES' button is clicked. #1
No more 'VIEW REPLIES' button to be clicked

1 ; https://www.instagram.com/p/CrTCPa7JWlJ/c/18087563071326842/ ; 2023-04-22 09:01:16 ; mei_story4 ; Selamat Hari Raya idul Fitri 🙏😇 ; 2023-04-21 12:01:13 ; https://www.instagram.com/p/CrTCPa7JWlJ/
2 ; https://www.instagram.com/p/CrTCPa7JWlJ/c/17

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 12.3 minutes

...Finished Scraping Instagram Permata Bank


Start Scraping Instagram CIMB Niaga...



'LOAD MORE COMMENTS' button is clicked. #1
No more 'LOAD MORE COMMENTS' button to be clicked

'VIEW REPLIES' button is clicked. #1
'VIEW REPLIES' button is clicked. #2
'VIEW REPLIES' button is clicked. #3
'VIEW REPLIES' button is clicked. #4
'VIEW REPLIES' button is clicked. #5
'VIEW REPLIES' button is clicked. #6
'VIEW REPLIES' button is clicked. #7
'VIEW REPLIES' button is clicked. #8
'VIEW REPLIES' button is clicked. #9
'VIEW REPLIES' button is clicked. #10
'VIEW REPLIES' button is clicked. #11
'VIEW REPLIES' button is clicked. #12
'VIEW REPLIES' button is clicked. #13
'VIEW REPLIES' button is clicked. #14
'VIEW REPLIES' button is clicked. #15
No more 'VIEW REPLIES' button to be clicked

1 ; https://www.instagram.com/p/CrUS0XhSEo4/c/17982448826095409/ ; 2023-04-23 12:00:53 ; mayaequaminity ; kenapa layanan telpon melalui internet di tiadakan????? sangat menyulitkan na

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 19.75 minutes

...Finished Scraping Instagram CIMB Niaga


Start Scraping Instagram Bank Danamon...



'LOAD MORE COMMENTS' button is clicked. #1
'LOAD MORE COMMENTS' button is clicked. #2
'LOAD MORE COMMENTS' button is clicked. #3
'LOAD MORE COMMENTS' button is clicked. #4
'LOAD MORE COMMENTS' button is clicked. #5
'LOAD MORE COMMENTS' button is clicked. #6
'LOAD MORE COMMENTS' button is clicked. #7
'LOAD MORE COMMENTS' button is clicked. #8
'LOAD MORE COMMENTS' button is clicked. #9
'LOAD MORE COMMENTS' button is clicked. #10
'LOAD MORE COMMENTS' button is clicked. #11
'LOAD MORE COMMENTS' button is clicked. #12
'LOAD MORE COMMENTS' button is clicked. #13
'LOAD MORE COMMENTS' button is clicked. #14
'LOAD MORE COMMENTS' button is clicked. #15
'LOAD MORE COMMENTS' button is clicked. #16
'LOAD MORE COMMENTS' button is clicked. #17
'LOAD MORE COMMENTS' button is clicked. #18
'LOAD MORE COMMENTS' button is clicked. #19
'LOAD MORE COMMENTS' button is clicked. #20
'LOAD MORE 

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 11.96 minutes

...Finished Scraping Instagram Bank Danamon



# Batch 3 (Seabank)

In [6]:
## 7. Bank Seabank
print('\nStart Scraping Instagram Seabank...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="seabank.id",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_seabank = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_seabank = df_seabank[df_seabank["name"] != "seabank.id\nVerified"]
df_seabank.reset_index(drop=True, inplace=True)
df_seabank["bank"] = "Seabank"
df_seabank["comment_date"] = datetime_format(df_seabank["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_seabank.to_excel(writer, sheet_name="Seabank")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram Seabank\n")

time.sleep(randtime_1*randtime_2)


Start Scraping Instagram Seabank...



'LOAD MORE COMMENTS' button is clicked. #1
'LOAD MORE COMMENTS' button is clicked. #2
'LOAD MORE COMMENTS' button is clicked. #3
'LOAD MORE COMMENTS' button is clicked. #4
'LOAD MORE COMMENTS' button is clicked. #5
'LOAD MORE COMMENTS' button is clicked. #6
'LOAD MORE COMMENTS' button is clicked. #7
'LOAD MORE COMMENTS' button is clicked. #8
'LOAD MORE COMMENTS' button is clicked. #9
'LOAD MORE COMMENTS' button is clicked. #10
'LOAD MORE COMMENTS' button is clicked. #11
'LOAD MORE COMMENTS' button is clicked. #12
'LOAD MORE COMMENTS' button is clicked. #13
'LOAD MORE COMMENTS' button is clicked. #14
'LOAD MORE COMMENTS' button is clicked. #15
'LOAD MORE COMMENTS' button is clicked. #16
'LOAD MORE COMMENTS' button is clicked. #17
'LOAD MORE COMMENTS' button is clicked. #18
'LOAD MORE COMMENTS' button is clicked. #19
'LOAD MORE COMMENTS' button is clicked. #20
'LOAD MORE COMMENTS' button is clicked. #21
'LOAD MORE COMMENTS' button is clicked. #22
'

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 73.97 minutes

...Finished Scraping Instagram Seabank



# Batch 3.1 (Blu, Neo)

In [7]:
## 8. Bank Blu Digital by BCA
print('\nStart Scraping Instagram Blu by BCA...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="blubybcadigital",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_blu = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_blu = df_blu[df_blu["name"] != "blubybcadigital\nVerified"]
df_blu.reset_index(drop=True, inplace=True)
df_blu["bank"] = "Blu by BCA"
df_blu["comment_date"] = datetime_format(df_blu["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_blu.to_excel(writer, sheet_name="Blu by BCA")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram Blu by BCA\n")

time.sleep(randtime_1*randtime_2)



## 9. Bank Neo Commerce
print('\nStart Scraping Instagram Neo Bank...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="bankneocommerce",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_neo = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_neo = df_neo[df_neo["name"] != "bankneocommerce\nVerified"]
df_neo.reset_index(drop=True, inplace=True)
df_neo["bank"] = "Neo Bank"
df_neo["comment_date"] = datetime_format(df_neo["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_neo.to_excel(writer, sheet_name="Neo Bank")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram Neo Bank\n")

time.sleep(randtime_1*randtime_2)


Start Scraping Instagram Blu by BCA...



No more 'LOAD MORE COMMENTS' button to be clicked

'VIEW REPLIES' button is clicked. #1
'VIEW REPLIES' button is clicked. #2
No more 'VIEW REPLIES' button to be clicked

1 ; https://www.instagram.com/p/CrTOgEBvFXv/c/18012256507543202/ ; 2023-04-23 01:47:02 ; sixty_seven_mack_elleven ; SoundCloud.com/sixty6seven7 ; 2023-04-21 13:47:42 ; https://www.instagram.com/p/CrTOgEBvFXv/
2 ; https://www.instagram.com/p/CrTOgEBvFXv/c/17973127895212335/ ; 2023-04-22 02:07:44 ; iro.sh04 ; Min cek DM ; 2023-04-21 13:47:42 ; https://www.instagram.com/p/CrTOgEBvFXv/
3 ; https://www.instagram.com/p/CrTOgEBvFXv/c/17980267187123186/ ; 2023-04-21 17:49:28 ; antonisastraa ; Min lama bangat sih kartu fisik nya 😢 ; 2023-04-21 13:47:42 ; https://www.instagram.com/p/CrTOgEBvFXv/


No more 'LOAD MORE COMMENTS' button to be clicked

No more 'VIEW REPLIES' button to be clicked

1 ; https://www.instagram.com/p/CrQW_env6qN/c/18056226289396754/ ; 2023-04-21 04:45:47 ; hpp_51k

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 5.72 minutes

...Finished Scraping Instagram Blu by BCA


Start Scraping Instagram Neo Bank...



No more 'LOAD MORE COMMENTS' button to be clicked

'VIEW REPLIES' button is clicked. #1
'VIEW REPLIES' button is clicked. #2
'VIEW REPLIES' button is clicked. #3
'VIEW REPLIES' button is clicked. #4
'VIEW REPLIES' button is clicked. #5
No more 'VIEW REPLIES' button to be clicked

4 ; https://www.instagram.com/p/CrYL0ekJF5u/c/17993515171745162/ ; 2023-04-23 12:01:10 ; fanbo114 ; Nama Aku ALFAN ; 2023-04-23 12:00:00 ; https://www.instagram.com/p/CrYL0ekJF5u/
6 ; https://www.instagram.com/p/CrYL0ekJF5u/c/18050371144423703/ ; 2023-04-23 12:01:04 ; fanbo114 ; Matur Sembah Nuwun Ngge ; 2023-04-23 12:00:00 ; https://www.instagram.com/p/CrYL0ekJF5u/
7 ; https://www.instagram.com/p/CrYL0ekJF5u/c/18057388036397010/ ; 2023-04-23 12:15:08 ; rezaherdiansyah23 ; Yg mau berteman di Neo boleh DM, untuk event untung jadi berkah ini Alhamdulillah lumayan dapetnya. Tapi belum tau siapa yg dpt 

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 11.41 minutes

...Finished Scraping Instagram Neo Bank



In [8]:
# ## 8. Bank Blu Digital by BCA
# print('\nStart Scraping Instagram Blu by BCA...\n')
# ## Time keeper
# start_time = time.time()

# user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="blubybcadigital",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

# df_blu = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
# df_blu = df_blu[df_blu["name"] != "blubybcadigital\nVerified"]
# df_blu.reset_index(drop=True, inplace=True)
# df_blu["bank"] = "Blu by BCA"
# df_blu["comment_date"] = datetime_format(df_blu["comment_date"])

# with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
#     # writer.book = openpyxl.load_workbook(path)
#     df_blu.to_excel(writer, sheet_name="Blu by BCA")

# ## Time keeper
# end_time = time.time()
# elapsed_time = (end_time - start_time)/60.0

# print("\nElapsed time:", round(elapsed_time,2), "minutes")
# print("\n...Finished Scraping Instagram Blu by BCA\n")

# time.sleep(randtime_1*randtime_2)



# ## 9. Bank Neo Commerce
# print('\nStart Scraping Instagram Neo Bank...\n')
# ## Time keeper
# start_time = time.time()

# user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="bankneocommerce",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

# df_neo = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
# df_neo = df_neo[df_neo["name"] != "bankneocommerce\nVerified"]
# df_neo.reset_index(drop=True, inplace=True)
# df_neo["bank"] = "Neo Bank"
# df_neo["comment_date"] = datetime_format(df_neo["comment_date"])

# with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
#     # writer.book = openpyxl.load_workbook(path)
#     df_neo.to_excel(writer, sheet_name="Neo Bank")

# ## Time keeper
# end_time = time.time()
# elapsed_time = (end_time - start_time)/60.0

# print("\nElapsed time:", round(elapsed_time,2), "minutes")
# print("\n...Finished Scraping Instagram Neo Bank\n")

# time.sleep(randtime_1*randtime_2)

In [9]:
# ## 9. Bank Neo Commerce
# print('\nStart Scraping Instagram Neo Bank...\n')
# ## Time keeper
# start_time = time.time()

# user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="bankneocommerce",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

# df_neo = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
# df_neo = df_neo[df_neo["name"] != "bankneocommerce\nVerified"]
# df_neo.reset_index(drop=True, inplace=True)
# df_neo["bank"] = "Neo Bank"
# df_neo["comment_date"] = datetime_format(df_neo["comment_date"])

# with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
#     # writer.book = openpyxl.load_workbook(path)
#     df_neo.to_excel(writer, sheet_name="Neo Bank")

# ## Time keeper
# end_time = time.time()
# elapsed_time = (end_time - start_time)/60.0

# print("\nElapsed time:", round(elapsed_time,2), "minutes")
# print("\n...Finished Scraping Instagram Neo Bank\n")

# Batch 4 (Jenius, Allo, Jago)

In [10]:
## 10. Jenius BTPN
print('\nStart Scraping Instagram Jenius...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="jeniusconnect",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_jenius = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_jenius = df_jenius[df_jenius["name"] != "jeniusconnect\nVerified"]
df_jenius.reset_index(drop=True, inplace=True)
df_jenius["bank"] = "Jenius"
df_jenius["comment_date"] = datetime_format(df_jenius["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_jenius.to_excel(writer, sheet_name="Jenius")


## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram Jenius\n")

time.sleep(randtime_1*randtime_2)



## 11. Allo Bank
print('\nStart Scraping Instagram Allo Bank...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="allobank",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_allo = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_allo = df_allo[df_allo["name"] != "allobank\nVerified"]
df_allo.reset_index(drop=True, inplace=True)
df_allo["bank"] = "Allo Bank"
df_allo["comment_date"] = datetime_format(df_allo["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_allo.to_excel(writer, sheet_name="Allo Bank")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram Allo Bank\n")

time.sleep(randtime_1*randtime_2)



## 12. Bank Jago
print('\nStart Scraping Instagram Bank Jago...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="jadijago",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_jago = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_jago = df_jago[df_jago["name"] != "jadijago\nVerified"]
df_jago.reset_index(drop=True, inplace=True)
df_jago ["bank"] = "Bank Jago"
df_jago["comment_date"] = datetime_format(df_jago["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_jago.to_excel(writer, sheet_name="Bank Jago")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram Bank Jago\n")

# time.sleep(randtime_1*randtime_2)


Start Scraping Instagram Jenius...



'LOAD MORE COMMENTS' button is clicked. #1
'LOAD MORE COMMENTS' button is clicked. #2
'LOAD MORE COMMENTS' button is clicked. #3
'LOAD MORE COMMENTS' button is clicked. #4
'LOAD MORE COMMENTS' button is clicked. #5
No more 'LOAD MORE COMMENTS' button to be clicked

'VIEW REPLIES' button is clicked. #1
'VIEW REPLIES' button is clicked. #2
'VIEW REPLIES' button is clicked. #3
'VIEW REPLIES' button is clicked. #4
'VIEW REPLIES' button is clicked. #5
'VIEW REPLIES' button is clicked. #6
'VIEW REPLIES' button is clicked. #7
'VIEW REPLIES' button is clicked. #8
'VIEW REPLIES' button is clicked. #9
'VIEW REPLIES' button is clicked. #10
'VIEW REPLIES' button is clicked. #11
'VIEW REPLIES' button is clicked. #12
'VIEW REPLIES' button is clicked. #13
'VIEW REPLIES' button is clicked. #14
'VIEW REPLIES' button is clicked. #15
'VIEW REPLIES' button is clicked. #16
'VIEW REPLIES' button is clicked. #17
'VIEW REPLIES' button is clicked. #18
'VIEW REPLIES' butto

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 6.89 minutes

...Finished Scraping Instagram Jenius


Start Scraping Instagram Allo Bank...



'LOAD MORE COMMENTS' button is clicked. #1
'LOAD MORE COMMENTS' button is clicked. #2
'LOAD MORE COMMENTS' button is clicked. #3
'LOAD MORE COMMENTS' button is clicked. #4
'LOAD MORE COMMENTS' button is clicked. #5
'LOAD MORE COMMENTS' button is clicked. #6
'LOAD MORE COMMENTS' button is clicked. #7
'LOAD MORE COMMENTS' button is clicked. #8
'LOAD MORE COMMENTS' button is clicked. #9
'LOAD MORE COMMENTS' button is clicked. #10
'LOAD MORE COMMENTS' button is clicked. #11
'LOAD MORE COMMENTS' button is clicked. #12
'LOAD MORE COMMENTS' button is clicked. #13
'LOAD MORE COMMENTS' button is clicked. #14
'LOAD MORE COMMENTS' button is clicked. #15
'LOAD MORE COMMENTS' button is clicked. #16
'LOAD MORE COMMENTS' button is clicked. #17
'LOAD MORE COMMENTS' button is clicked. #18
'LOAD MORE COMMENTS' button is clicked. #19
'LOAD MORE COMMENTS' button is clicked. #20
'LOAD MORE COMMENTS

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 82.24 minutes

...Finished Scraping Instagram Allo Bank


Start Scraping Instagram Bank Jago...



No more 'LOAD MORE COMMENTS' button to be clicked

'VIEW REPLIES' button is clicked. #1
'VIEW REPLIES' button is clicked. #2
'VIEW REPLIES' button is clicked. #3
No more 'VIEW REPLIES' button to be clicked

1 ; https://www.instagram.com/p/CrUiUlwrRsT/c/17853487130953294/ ; 2023-04-22 22:10:33 ; yvdhi__ ; mon maaf lahir batin mz @cornelius_krishna ; 2023-04-22 02:00:08 ; https://www.instagram.com/p/CrUiUlwrRsT/
2 ; https://www.instagram.com/p/CrUiUlwrRsT/c/18287322820110711/ ; 2023-04-22 14:34:27 ; pecintacatur.id ; Hallo Min @jadijago kantong terkunci gak bisa undang teman ya? Jadi bisa undang teman kalau kantong itu hanya kantong nabung aja? ; 2023-04-22 02:00:08 ; https://www.instagram.com/p/CrUiUlwrRsT/
3 ; https://www.instagram.com/p/CrUiUlwrRsT/c/18015272335570934/ ; 2023-04-22 12:50:06 ; seran.herman ; Semoga secepatnya jago punya KTA buat nasabah2nya🙌 ; 2023-04-22 02

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 9.26 minutes

...Finished Scraping Instagram Bank Jago



# Batch 5 (BNI, BCA, BRI)

In [11]:
## 13. BNI
print('\nStart Scraping Instagram BNI...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="bni46",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_bni = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_bni = df_bni[df_bni["name"] != "bni46\nVerified"]
df_bni.reset_index(drop=True, inplace=True)
df_bni["bank"] = "BNI"
df_bni["comment_date"] = datetime_format(df_bni["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_bni.to_excel(writer, sheet_name="BNI")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram BNI\n")

time.sleep(randtime_1*randtime_2)



## 14. BCA
print('\nStart Scraping Instagram BCA...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="goodlifebca",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_bca = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_bca = df_bca[df_bca["name"] != "goodlifebca\nVerified"]
# df_bca.reset_index(drop=True, inplace=True)
df_bca["bank"] = "BCA"
df_bca["comment_date"] = datetime_format(df_bca["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_bca.to_excel(writer, sheet_name="BCA")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram BCA\n")

time.sleep(randtime_1*randtime_2)


## 15. BRI
print('\nStart Scraping Instagram BRI...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="bankbri_id",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_bri = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_bri = df_bri[df_bri["name"] != "bankbri_id\nVerified"]
df_bri.reset_index(drop=True, inplace=True)
df_bri["bank"] = "BRI"
df_bri["comment_date"] = datetime_format(df_bri["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_bri.to_excel(writer, sheet_name="BRI")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram BRI\n")

time.sleep(randtime_1*randtime_2)


Start Scraping Instagram BNI...



'LOAD MORE COMMENTS' button is clicked. #1
'LOAD MORE COMMENTS' button is clicked. #2
No more 'LOAD MORE COMMENTS' button to be clicked

'VIEW REPLIES' button is clicked. #1
'VIEW REPLIES' button is clicked. #2
'VIEW REPLIES' button is clicked. #3
'VIEW REPLIES' button is clicked. #4
'VIEW REPLIES' button is clicked. #5
'VIEW REPLIES' button is clicked. #6
'VIEW REPLIES' button is clicked. #7
'VIEW REPLIES' button is clicked. #8
'VIEW REPLIES' button is clicked. #9
'VIEW REPLIES' button is clicked. #10
'VIEW REPLIES' button is clicked. #11
'VIEW REPLIES' button is clicked. #12
'VIEW REPLIES' button is clicked. #13
'VIEW REPLIES' button is clicked. #14
'VIEW REPLIES' button is clicked. #15
'VIEW REPLIES' button is clicked. #16
'VIEW REPLIES' button is clicked. #17
'VIEW REPLIES' button is clicked. #18
'VIEW REPLIES' button is clicked. #19
'VIEW REPLIES' button is clicked. #20
'VIEW REPLIES' button is clicked. #21
No more 'VIEW REPLIES' button to be cl

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 34.56 minutes

...Finished Scraping Instagram BNI


Start Scraping Instagram BCA...



'LOAD MORE COMMENTS' button is clicked. #1
'LOAD MORE COMMENTS' button is clicked. #2
'LOAD MORE COMMENTS' button is clicked. #3
'LOAD MORE COMMENTS' button is clicked. #4
No more 'LOAD MORE COMMENTS' button to be clicked

'VIEW REPLIES' button is clicked. #1
'VIEW REPLIES' button is clicked. #2
'VIEW REPLIES' button is clicked. #3
'VIEW REPLIES' button is clicked. #4
'VIEW REPLIES' button is clicked. #5
'VIEW REPLIES' button is clicked. #6
'VIEW REPLIES' button is clicked. #7
'VIEW REPLIES' button is clicked. #8
'VIEW REPLIES' button is clicked. #9
'VIEW REPLIES' button is clicked. #10
'VIEW REPLIES' button is clicked. #11
'VIEW REPLIES' button is clicked. #12
'VIEW REPLIES' button is clicked. #13
'VIEW REPLIES' button is clicked. #14
'VIEW REPLIES' button is clicked. #15
'VIEW REPLIES' button is clicked. #16
'VIEW REPLIES' button is clicked. #17
'VIEW REPLIES' button is clicked. #18


C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 54.99 minutes

...Finished Scraping Instagram BCA


Start Scraping Instagram BRI...



'LOAD MORE COMMENTS' button is clicked. #1
'LOAD MORE COMMENTS' button is clicked. #2
'LOAD MORE COMMENTS' button is clicked. #3
'LOAD MORE COMMENTS' button is clicked. #4
'LOAD MORE COMMENTS' button is clicked. #5
'LOAD MORE COMMENTS' button is clicked. #6
'LOAD MORE COMMENTS' button is clicked. #7
'LOAD MORE COMMENTS' button is clicked. #8
'LOAD MORE COMMENTS' button is clicked. #9
'LOAD MORE COMMENTS' button is clicked. #10
'LOAD MORE COMMENTS' button is clicked. #11
'LOAD MORE COMMENTS' button is clicked. #12
'LOAD MORE COMMENTS' button is clicked. #13
'LOAD MORE COMMENTS' button is clicked. #14
'LOAD MORE COMMENTS' button is clicked. #15
'LOAD MORE COMMENTS' button is clicked. #16
'LOAD MORE COMMENTS' button is clicked. #17
'LOAD MORE COMMENTS' button is clicked. #18
'LOAD MORE COMMENTS' button is clicked. #19
'LOAD MORE COMMENTS' button is clicked. #20
'LOAD MORE COMMENTS' button

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 314.31 minutes

...Finished Scraping Instagram BRI



# Batch 6 (Mandiri)

In [12]:
## 16. Mandiri
print('\nStart Scraping Instagram Bank Mandiri...\n')
## Time keeper
start_time = time.time()

user_names, comment_ids, user_comments, post_date, post_url, comment_date = get_comments(username="bankmandiri",  driver=driver, cutoff_awal = cutoff_awal, cutoff_akhir = cutoff_akhir ,comment_awal = comment_awal, comment_akhir = comment_akhir)

df_mandiri = pd.DataFrame(list(zip(user_names, comment_ids, user_comments, post_date, post_url, comment_date)), columns=["name","comment_id","comments","post_date","post_url","comment_date"])
df_mandiri = df_mandiri[df_mandiri["name"] != "bankmandiri\nVerified"]
df_mandiri.reset_index(drop=True, inplace=True)
df_mandiri["bank"] = "Bank Mandiri"
df_mandiri["comment_date"] = datetime_format(df_mandiri["comment_date"])

with pd.ExcelWriter(path, mode='a', engine='openpyxl') as writer:
    # writer.book = openpyxl.load_workbook(path)
    df_mandiri.to_excel(writer, sheet_name="Bank Mandiri")

## Time keeper
end_time = time.time()
elapsed_time = (end_time - start_time)/60.0

print("\nElapsed time:", round(elapsed_time,2), "minutes")
print("\n...Finished Scraping Instagram Bank Mandiri\n")

time.sleep(randtime_1*randtime_2)


Start Scraping Instagram Bank Mandiri...



No more 'LOAD MORE COMMENTS' button to be clicked

No more 'VIEW REPLIES' button to be clicked



No more 'LOAD MORE COMMENTS' button to be clicked

No more 'VIEW REPLIES' button to be clicked



'LOAD MORE COMMENTS' button is clicked. #1
'LOAD MORE COMMENTS' button is clicked. #2
'LOAD MORE COMMENTS' button is clicked. #3
'LOAD MORE COMMENTS' button is clicked. #4
No more 'LOAD MORE COMMENTS' button to be clicked

'VIEW REPLIES' button is clicked. #1
'VIEW REPLIES' button is clicked. #2
'VIEW REPLIES' button is clicked. #3
'VIEW REPLIES' button is clicked. #4
'VIEW REPLIES' button is clicked. #5
'VIEW REPLIES' button is clicked. #6
'VIEW REPLIES' button is clicked. #7
'VIEW REPLIES' button is clicked. #8
'VIEW REPLIES' button is clicked. #9
'VIEW REPLIES' button is clicked. #10
'VIEW REPLIES' button is clicked. #11
'VIEW REPLIES' button is clicked. #12
'VIEW REPLIES' button is clicked. #13
'VIEW REPLIES' button is clicked. #14
'VIEW REPLIES

C:\Users\Ref\AppData\Local\Temp\ipykernel_6996\1547816477.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  comment_date_column[i] = (comment_date_column[i] + datetime.timedelta(hours=7)).strftime("%Y-%m-%d")



Elapsed time: 35.41 minutes

...Finished Scraping Instagram Bank Mandiri

